In [49]:
import py2neo
print(py2neo.__version__)

4.0.0b2


In [68]:
# python libraries
from py2neo import Graph
import numpy as np 
from pandas import DataFrame
import itertools
import matplotlib.pyplot as plt
import seaborn as sns
import json
import math
import pandas as pd
# import plotly 
# import plotly.graph_objs as go
# import qgrid
from scipy import stats, spatial
from scipy.sparse import csr_matrix
from sklearn.cluster.bicluster import SpectralBiclustering
import scipy.spatial as sp, scipy.cluster.hierarchy as hc, scipy.sparse.csgraph as csgraph
import operator
from IPython.display import display, HTML
from matplotlib.colors import ListedColormap
import pickle


# connection to Neo4j
local_connection_url = "http://localhost:7474/db/data"
connection_to_graph = Graph(local_connection_url, user="neo4j", password="zxc397") 

# plotly credentials
# plotly_config = json.load(open('plotly_config.json'))
# plotly.tools.set_credentials_file(username=plotly_config['username'], api_key=plotly_config['key'])

In [51]:
f_terms = list(set(DataFrame(connection_to_graph.data('MATCH (a:Asset)-[:CONTAINS]->(fs:Feedstock) RETURN  fs.term, count(a)')).as_matrix()[:, 1]))
o_terms = list(set(DataFrame(connection_to_graph.data('MATCH (a:Asset)-[:CONTAINS]->(fs:Output) RETURN  fs.term, count(a)')).as_matrix()[:, 1]))
pt_terms = list(set(DataFrame(connection_to_graph.data('MATCH (a:Asset)-[:CONTAINS]->(fs:ProcessingTech) RETURN  fs.term, count(a)')).as_matrix()[:, 1]))
bbo = list(f_terms + pt_terms + o_terms)
print ("Number of terms:", len(bbo))
nodes = bbo
print(nodes)

('Number of terms:', 352)
[u'vegetable oil', u'recycled ethanol', u'woodwaste/bagasse', u'natural gas', u'various grasses', u'nonedible oils', u'animal fats', u'paper', u'ponderosa pine', u'grass seed', u'sulfite spent liquor from spruce wood pulping', u'osb', u'paper waste', u'corn cob', u'energy grasses', u'logging residues', u'willow', u'crop waste', u'firewood', u'jatropha', u'sugarcane bagasse', u'sugar', u'durum', u'wood', u'municipal solid waste', u'banna grass', u'waste oil', u'cassava pulp', u'barley', u'mixed oilseeds', u'starch', u'white grease', u'coniferous wood', u'corn oil', u'wood waste', u'mixed cellulose', u'corn stalks', u'yellow grease', u'molasses', u'woodchips', u'food waste', u'citrus residues', u'wood chips', u'spent sulphite liquor feedstock', u'palm, rapeseed oil, waste fat', u'cotton residue', u'industrial waste', u'deciduous forests', u'corn stover', u'cereals/sugar', u'waste fat', u'waste vegetable oil', u'tallow', u'sewage', u'white pine', u'hardwood', u'b

In [52]:
#Remove leading spaces
newnodes = list()
for node in nodes:
    newnode = node.lstrip()
    newnodes.append(newnode)
nodes=newnodes
nodes

[u'vegetable oil',
 u'recycled ethanol',
 u'woodwaste/bagasse',
 u'natural gas',
 u'various grasses',
 u'nonedible oils',
 u'animal fats',
 u'paper',
 u'ponderosa pine',
 u'grass seed',
 u'sulfite spent liquor from spruce wood pulping',
 u'osb',
 u'paper waste',
 u'corn cob',
 u'energy grasses',
 u'logging residues',
 u'willow',
 u'crop waste',
 u'firewood',
 u'jatropha',
 u'sugarcane bagasse',
 u'sugar',
 u'durum',
 u'wood',
 u'municipal solid waste',
 u'banna grass',
 u'waste oil',
 u'cassava pulp',
 u'barley',
 u'mixed oilseeds',
 u'starch',
 u'white grease',
 u'coniferous wood',
 u'corn oil',
 u'wood waste',
 u'mixed cellulose',
 u'corn stalks',
 u'yellow grease',
 u'molasses',
 u'woodchips',
 u'food waste',
 u'citrus residues',
 u'wood chips',
 u'spent sulphite liquor feedstock',
 u'palm, rapeseed oil, waste fat',
 u'cotton residue',
 u'industrial waste',
 u'deciduous forests',
 u'corn stover',
 u'cereals/sugar',
 u'waste fat',
 u'waste vegetable oil',
 u'tallow',
 u'sewage',
 u'w

In [53]:
#REMOVAL/ADDITION - find nodes with commas, separate them and add to nodelist if not in there, remove the unseparated node
print len(nodes)
for node in nodes:
    if "," in node:
        separates = node.split(",")
        for separate in separates:
            #remove leading space if any
            separate = separate.lstrip()
            if separate not in nodes:
                nodes.append(separate)
                print separate
        #remove unseparated node from list
        nodes.remove(node)
print len(nodes)
print nodes

352
methanol synthesis
mtg catalysis
fibers
polylutylene succinate
bioplymers from corn
potatoes
tapioca
renewable diesel from animal fats
veggie oils
352
[u'vegetable oil', u'recycled ethanol', u'woodwaste/bagasse', u'natural gas', u'various grasses', u'nonedible oils', u'animal fats', u'paper', u'ponderosa pine', u'grass seed', u'sulfite spent liquor from spruce wood pulping', u'osb', u'paper waste', u'corn cob', u'energy grasses', u'logging residues', u'willow', u'crop waste', u'firewood', u'jatropha', u'sugarcane bagasse', u'sugar', u'durum', u'wood', u'municipal solid waste', u'banna grass', u'waste oil', u'cassava pulp', u'barley', u'mixed oilseeds', u'starch', u'white grease', u'coniferous wood', u'corn oil', u'wood waste', u'mixed cellulose', u'corn stalks', u'yellow grease', u'molasses', u'woodchips', u'food waste', u'citrus residues', u'wood chips', u'spent sulphite liquor feedstock', u'cotton residue', u'industrial waste', u'deciduous forests', u'corn stover', u'cereals/suga

In [54]:
#REMOVAL - all edges with NULL Years
feedproc = connection_to_graph.data('MATCH p2=(feed:Feedstock)<-[:CONTAINS]-(n:Asset)-[:CONTAINS]->(proc:ProcessingTech) WHERE (n.year)<>"Null" RETURN n.id, n.year, feed.term, proc.term')
feedout = connection_to_graph.data('MATCH p2=(feed:Feedstock)<-[:CONTAINS]-(n:Asset)-[:CONTAINS]->(out:Output) WHERE (n.year)<>"Null" RETURN n.id, n.year, feed.term, out.term')
procout = connection_to_graph.data('MATCH p2=(proc:ProcessingTech)<-[:CONTAINS]-(n:Asset)-[:CONTAINS]->(out:Output) WHERE (n.year)<>"Null" RETURN n.id, n.year, proc.term, out.term')
df1 = pd.DataFrame(feedproc)
df2 = pd.DataFrame(feedout)
df3 = pd.DataFrame(procout)

In [55]:
edgelist = []
for index, row in df1.iterrows():
    rowstr = row[u'feed.term'].lstrip() + "," + row[u'proc.term'].lstrip() + "," + row[u'n.year']
    #edgelist = edgelist + str
    edgelist.append(rowstr)
# print "df2-------------"
for index, row in df2.iterrows():
    rowstr = row[u'feed.term'].lstrip() + "," + row[u'out.term'].lstrip() + "," + row[u'n.year']
    edgelist.append(rowstr)
    #edgelist = edgelist + str
# print "df3-------------"
for index, row in df3.iterrows():
    rowstr = row[u'proc.term'].lstrip() + "," + row[u'out.term'].lstrip() + "," + row[u'n.year']
    edgelist.append(rowstr)
    #edgelist = edgelist + str
edgelist

[u'cooking oil,solvents,2011',
 u'waste,solvents,2011',
 u'waste,solvents,2012',
 u'industrial waste,solvents,2012',
 u'free fatty acid,solvents,2012',
 u'corn stover,solvents,2016',
 u'stover,solvents,2016',
 u'sugar,solvents,2016',
 u'corn,solvents,2016',
 u'cellulose,solvents,2016',
 u'cellulosic biomass,solvents,2016',
 u'cellulose,solvents,2012',
 u'douglas fir,solvents,2014',
 u'wood,solvents,2014',
 u'woody biomass,solvents,2014',
 u'cellulose,solvents,2014',
 u'pine,solvents,2013',
 u'wood,solvents,2013',
 u'sawdust,solvents,2013',
 u'waste water,solvents,2014',
 u'algae,solvents,2014',
 u'waste,solvents,2014',
 u'waste water,solvents,2016',
 u'palm,solvents,2016',
 u'waste,solvents,2016',
 u'sewage,solvents,2016',
 u'vegetable oil,solvents,2017',
 u'cooking oil,solvents,2017',
 u'waste,solvents,2017',
 u'waste,solvents,2016',
 u'waste water,solvents,2011',
 u'algae,solvents,2011',
 u'pal waste,solvents,2011',
 u'waste,solvents,2011',
 u'sewage,solvents,2011',
 u'algae,solvents

In [56]:
df = pd.DataFrame({'edges':edgelist}) #convert list to dataframe

In [57]:
# convert into weighted edgelist - count occurences for each edge
df['source'], df['target'], df['year'] = df['edges'].str.split(',', 2).str
weighted = df.groupby(['edges','source','target','year']).size().reset_index(name='count')
#weightedless = df.groupby(['edges']).size().reset_index(name='count')
#weightedless
weighted

edges  \
0                       Giant reed,advanced biofuel,2013   
1                    Giant reed,anaerobic digestion,2014   
2                    Giant reed,anaerobic digestion,2015   
3                    Giant reed,anaerobic digestion,2016   
4                              Giant reed,biodiesel,2011   
5                              Giant reed,biodiesel,2012   
6                                 Giant reed,biogas,2012   
7                                 Giant reed,biogas,2014   
8                                 Giant reed,biogas,2016   
9                                Giant reed,butanol,2012   
10                             Giant reed,catalysis,2013   
11                  Giant reed,enzymatic hydrolysis,2015   
12                               Giant reed,ethanol,2011   
13                               Giant reed,ethanol,2012   
14                               Giant reed,ethanol,2015   
15                          Giant reed,fermentation,2013   
16                          Giant reed,fermentation,2014   
17                          Giant reed,fermentation,2016   
18                            Giant reed,hydrolysis,2014   
19                            Giant reed,hydrolysis,2015   
20                            Giant reed,hydrolysis,2016   
21                              Giant reed,pressing,2011   
22                              Giant reed,pressing,2012   
23                 acid hydrolysis,advanced biofuel,2015   
24                 acid hydrolysis,advanced biofuel,2016   
25                 acid hydrolysis,advanced biofuel,2017   
26                          acid hydrolysis,bio-oil,2010   
27                          acid hydrolysis,bio-oil,2011   
28                          acid hydrolysis,bio-oil,2014   
29                          acid hydrolysis,bio-oil,2016   
30                          acid hydrolysis,bio-oil,2017   
31                       acid hydrolysis,biobutanol,2013   
32                       acid hydrolysis,biobutanol,2014   
33                        acid hydrolysis,biodiesel,2011   
34                        acid hydrolysis,biodiesel,2012   
35                        acid hydrolysis,biodiesel,2013   
36                        acid hydrolysis,biodiesel,2014   
37                        acid hydrolysis,biodiesel,2015   
38                        acid hydrolysis,biodiesel,2016   
39                       acid hydrolysis,bioethanol,2010   
40                       acid hydrolysis,bioethanol,2011   
41                       acid hydrolysis,bioethanol,2012   
42                       acid hydrolysis,bioethanol,2013   
43                       acid hydrolysis,bioethanol,2014   
44                       acid hydrolysis,bioethanol,2015   
45                       acid hydrolysis,bioethanol,2016   
46           acid hydrolysis,biofuels for transport,2010   
47                           acid hydrolysis,biogas,2010   
48                           acid hydrolysis,biogas,2014   
49                          acid hydrolysis,butanol,2010   
50                          acid hydrolysis,butanol,2013   
51                          acid hydrolysis,butanol,2014   
52                          acid hydrolysis,butanol,2016   
53               acid hydrolysis,cellulosic biofuel,2012   
54               acid hydrolysis,cellulosic biofuel,2013   
55               acid hydrolysis,cellulosic biofuel,2015   
56               acid hydrolysis,cellulosic ethanol,2007   
57               acid hydrolysis,cellulosic ethanol,2010   
58               acid hydrolysis,cellulosic ethanol,2011   
59               acid hydrolysis,cellulosic ethanol,2013   
60                          acid hydrolysis,ethanol,2007   
61                          acid hydrolysis,ethanol,2010   
62                          acid hydrolysis,ethanol,2011   
63                          acid hydrolysis,ethanol,2012   
64                          acid hydrolysis,ethanol,2013   
65                          acid hydrolysis,ethanol,2014   
66                          aci

In [84]:
pickle_out = open("weighted.pickle","wb")
pickle.dump(weighted, pickle_out)
pickle_out.close()

In [85]:
pickle_in = open("weighted.pickle","rb")
weighted = pickle.load(pickle_in)
weighted

edges  \
0                       Giant reed,advanced biofuel,2013   
1                    Giant reed,anaerobic digestion,2014   
2                    Giant reed,anaerobic digestion,2015   
3                    Giant reed,anaerobic digestion,2016   
4                              Giant reed,biodiesel,2011   
5                              Giant reed,biodiesel,2012   
6                                 Giant reed,biogas,2012   
7                                 Giant reed,biogas,2014   
8                                 Giant reed,biogas,2016   
9                                Giant reed,butanol,2012   
10                             Giant reed,catalysis,2013   
11                  Giant reed,enzymatic hydrolysis,2015   
12                               Giant reed,ethanol,2011   
13                               Giant reed,ethanol,2012   
14                               Giant reed,ethanol,2015   
15                          Giant reed,fermentation,2013   
16                          Giant reed,fermentation,2014   
17                          Giant reed,fermentation,2016   
18                            Giant reed,hydrolysis,2014   
19                            Giant reed,hydrolysis,2015   
20                            Giant reed,hydrolysis,2016   
21                              Giant reed,pressing,2011   
22                              Giant reed,pressing,2012   
23                 acid hydrolysis,advanced biofuel,2015   
24                 acid hydrolysis,advanced biofuel,2016   
25                 acid hydrolysis,advanced biofuel,2017   
26                          acid hydrolysis,bio-oil,2010   
27                          acid hydrolysis,bio-oil,2011   
28                          acid hydrolysis,bio-oil,2014   
29                          acid hydrolysis,bio-oil,2016   
30                          acid hydrolysis,bio-oil,2017   
31                       acid hydrolysis,biobutanol,2013   
32                       acid hydrolysis,biobutanol,2014   
33                        acid hydrolysis,biodiesel,2011   
34                        acid hydrolysis,biodiesel,2012   
35                        acid hydrolysis,biodiesel,2013   
36                        acid hydrolysis,biodiesel,2014   
37                        acid hydrolysis,biodiesel,2015   
38                        acid hydrolysis,biodiesel,2016   
39                       acid hydrolysis,bioethanol,2010   
40                       acid hydrolysis,bioethanol,2011   
41                       acid hydrolysis,bioethanol,2012   
42                       acid hydrolysis,bioethanol,2013   
43                       acid hydrolysis,bioethanol,2014   
44                       acid hydrolysis,bioethanol,2015   
45                       acid hydrolysis,bioethanol,2016   
46           acid hydrolysis,biofuels for transport,2010   
47                           acid hydrolysis,biogas,2010   
48                           acid hydrolysis,biogas,2014   
49                          acid hydrolysis,butanol,2010   
50                          acid hydrolysis,butanol,2013   
51                          acid hydrolysis,butanol,2014   
52                          acid hydrolysis,butanol,2016   
53               acid hydrolysis,cellulosic biofuel,2012   
54               acid hydrolysis,cellulosic biofuel,2013   
55               acid hydrolysis,cellulosic biofuel,2015   
56               acid hydrolysis,cellulosic ethanol,2007   
57               acid hydrolysis,cellulosic ethanol,2010   
58               acid hydrolysis,cellulosic ethanol,2011   
59               acid hydrolysis,cellulosic ethanol,2013   
60                          acid hydrolysis,ethanol,2007   
61                          acid hydrolysis,ethanol,2010   
62                          acid hydrolysis,ethanol,2011   
63                          acid hydrolysis,ethanol,2012   
64                          acid hydrolysis,ethanol,2013   
65                          acid hydrolysis,ethanol,2014   
66                          aci

In [58]:
#TODO - REWRITE THIS AS FOR ONE YEAR
#REMOVAL - remove nodes from nodelist that are not in edges
print len(nodes)
toremove = []
for node in nodes:
    i = 0
    #check if node is in source
    for source in df['source']:
        if node == source:
            i = 1
    #check if node is in source
    for target in df['target']:
        if node == target:
            i = 1
    if i == 0:
        toremove.append(node)
        nodes.remove(node)
print (toremove)
print (len(nodes))

352
[u'recycled ethanol', u'sulfite spent liquor from spruce wood pulping', u'durum', u'cassava pulp', u'mixed oilseeds', u'white grease', u'mixed cellulose', u'spent sulphite liquor feedstock', u'deciduous forests', u'cereals/sugar', u'biogas from municipal wastewater treatment facility digesters', u'stump material', u'animal residue', u'fall rye', u'fat products', u'soft white spring wheat', u'mixed grass', u'poppy seed', u'multi feedstock', u'palm stearin', u'mixedwood', u'corn sugar', u'feed wheat', u'juncea oil', u'barley starch', u'Decommissioned electricity poles and railway ties', u'cps wheat', u'radiate pine', u'red pine', u'biogenic waste oils', u'bagasse/cane trash', u'wood processing residues', u'natural fats', u'steel waste gas (co)', u'flaxseed oil', u'corn/milo', u'non-food grade canola oil', u'algae transesterification', u'solar conversion', u'chemprocessing', u'orc process', u'btl - syngas', u'algae burning/transesterifcation', u'steam reform/ft', u'algae oil hydrotrea

## Create dump of a nodelist for future use

In [72]:
pickle_out = open("nodes.pickle","wb")
pickle.dump(nodes, pickle_out)
pickle_out.close()

In [73]:
pickle_in = open("nodes.pickle","rb")
nodes = pickle.load(pickle_in)
nodes

[u'vegetable oil',
 u'woodwaste/bagasse',
 u'natural gas',
 u'various grasses',
 u'nonedible oils',
 u'animal fats',
 u'paper',
 u'ponderosa pine',
 u'grass seed',
 u'osb',
 u'paper waste',
 u'corn cob',
 u'energy grasses',
 u'logging residues',
 u'willow',
 u'crop waste',
 u'firewood',
 u'jatropha',
 u'sugarcane bagasse',
 u'sugar',
 u'wood',
 u'municipal solid waste',
 u'banna grass',
 u'waste oil',
 u'barley',
 u'starch',
 u'coniferous wood',
 u'corn oil',
 u'wood waste',
 u'corn stalks',
 u'yellow grease',
 u'molasses',
 u'woodchips',
 u'food waste',
 u'citrus residues',
 u'wood chips',
 u'cotton residue',
 u'industrial waste',
 u'corn stover',
 u'waste fat',
 u'waste vegetable oil',
 u'tallow',
 u'sewage',
 u'white pine',
 u'hardwood',
 u'loblolly pine',
 u'miscanthus',
 u'palm',
 u'milo',
 u'bark',
 u'agriculture',
 u'textiles',
 u'beef tallow',
 u'animal waste',
 u'cobs',
 u'forest residues',
 u'grass clippings',
 u'plywood',
 u'dry biomass',
 u'southern yellow pine',
 u'free fa

In [61]:
#nodeindex = {0:'zero',1:'one'}
#create dictionary to map indexes to nodes
nodeindex = {}
for i in range(len(nodes)):
    nodeindex[i] = nodes[i]
nodeindex

{0: u'vegetable oil',
 1: u'woodwaste/bagasse',
 2: u'natural gas',
 3: u'various grasses',
 4: u'nonedible oils',
 5: u'animal fats',
 6: u'paper',
 7: u'ponderosa pine',
 8: u'grass seed',
 9: u'osb',
 10: u'paper waste',
 11: u'corn cob',
 12: u'energy grasses',
 13: u'logging residues',
 14: u'willow',
 15: u'crop waste',
 16: u'firewood',
 17: u'jatropha',
 18: u'sugarcane bagasse',
 19: u'sugar',
 20: u'wood',
 21: u'municipal solid waste',
 22: u'banna grass',
 23: u'waste oil',
 24: u'barley',
 25: u'starch',
 26: u'coniferous wood',
 27: u'corn oil',
 28: u'wood waste',
 29: u'corn stalks',
 30: u'yellow grease',
 31: u'molasses',
 32: u'woodchips',
 33: u'food waste',
 34: u'citrus residues',
 35: u'wood chips',
 36: u'cotton residue',
 37: u'industrial waste',
 38: u'corn stover',
 39: u'waste fat',
 40: u'waste vegetable oil',
 41: u'tallow',
 42: u'sewage',
 43: u'white pine',
 44: u'hardwood',
 45: u'loblolly pine',
 46: u'miscanthus',
 47: u'palm',
 48: u'milo',
 49: u'b

In [62]:
# create matrix with zeros with size nodes x nodes
pd.set_option('display.max_columns', 500)
pd.set_option('display.max_rows', 500)
zero_data = np.zeros(shape=(len(nodes),len(nodes)))
adjacency = pd.DataFrame(zero_data, index = nodeindex, columns=nodes)
adjacency.rename(index=nodeindex, inplace=True)
#d.rename(nodes, axis='index')
#dists.at[' aerobic digestion',' aerobic digestion'] = 1

In [63]:
if "anaerobic digestion" in nodes:
    print "yes"
else:
    print "no"

yes


In [74]:
#fill adjacency matrix with actual distances, i.e. edge weights
#for each row in edgelist df 
    #put count into source/target cell in distmatrix / d.at[nodes.index(source),target] = count
for index, row in weighted.iterrows():
    #if nodes.isin(row.source) and nodes.isin(row.target) :
    #print row['count']
    if row.source in nodes and row.target in nodes:
        adjacency.at[row.source,row.target] = row['count']
        adjacency.at[row.target,row.source] = row['count']
    else:
        print (row.source + ":" + row.target)

corn stover: cobs
corn stover: cobs
corn stover: cobs
corn stover: cobs
rice straw: corn stalks
rice straw: corn stalks
rice straw: corn stalks


## Create dump of a weighted adjacency matrix for future use

In [75]:
pickle_out = open("adjacency.pickle","wb")
pickle.dump(adjacency, pickle_out)
pickle_out.close()

In [76]:
pickle_in = open("adjacency.pickle","rb")
adjacency = pickle.load(pickle_in)
adjacency

vegetable oil  woodwaste/bagasse  \
vegetable oil                                 0.0                0.0   
woodwaste/bagasse                             0.0                0.0   
natural gas                                   0.0                0.0   
various grasses                               0.0                0.0   
nonedible oils                                0.0                0.0   
animal fats                                   0.0                0.0   
paper                                         0.0                0.0   
ponderosa pine                                0.0                0.0   
grass seed                                    0.0                0.0   
osb                                           0.0                0.0   
paper waste                                   0.0                0.0   
corn cob                                      0.0                0.0   
energy grasses                                0.0                0.0   
logging residues                              0.0                0.0   
willow                                        0.0                0.0   
crop waste                                    0.0                0.0   
firewood                                      0.0                0.0   
jatropha                                      0.0                0.0   
sugarcane bagasse                             0.0                0.0   
sugar                                         0.0                0.0   
wood                                          0.0                0.0   
municipal solid waste                         0.0                0.0   
banna grass                                   0.0                0.0   
waste oil                                     0.0                0.0   
barley                                        0.0                0.0   
starch                                        0.0                0.0   
coniferous wood                               0.0                0.0   
corn oil                                      0.0                0.0   
wood waste                                    0.0                0.0   
corn stalks                                   0.0                0.0   
yellow grease                                 0.0                0.0   
molasses                                      0.0                0.0   
woodchips                                     0.0                0.0   
food waste                                    0.0                0.0   
citrus residues                               0.0                0.0   
wood chips                                    0.0                0.0   
cotton residue                                0.0                0.0   
industrial waste                              0.0                0.0   
corn stover                                   0.0                0.0   
waste fat                                     0.0                0.0   
waste vegetable oil                           0.0                0.0   
tallow                                        0.0                0.0   
sewage                                        0.0                0.0   
white pine                                    0.0                0.0   
hardwood                                      0.0                0.0   
loblolly pine                                 0.0                0.0   
miscanthus                                    0.0                0.0   
palm                                          0.0                0.0   
milo                                          0.0                0.0   
bark                                          0.0                0.0   
agriculture                                   0.0                0.0   
textiles                                      0.0                0.0   
beef tallow                                   0.0                0.0   
animal waste                                  0.0                0.0   
cobs                                          0.0                0.0   
fore

In [77]:
#restore clustering from iGraph dump
pickle_in = open("clusts.pickle","rb")
clusts = pickle.load(pickle_in)
clusts

In [78]:
#restore clustering from iGraph
#x['a'] = 1
#%store -r clusts
clusts_nodes = dict()
for i, cluster in enumerate(clusts):
#     print ("Cluster: " + str(i))
#     print ("Size: " + str(len(cluster)))
    cnodes = list()
    for item in cluster:
        #print(nodes[item])
        #add node names to cluster
        cnodes.append(nodes[item])
    #print ("\n")
    clusts_nodes[i]=cnodes
#print# clusts_nodes

In [79]:
#swap keys with values
nodesdict = dict()
for key, values in clusts_nodes.iteritems():
    for value in values:
        nodesdict[value] = key
#nodesdict

In [80]:
col_names =  ['year', 'node', 'count','clusterID']
my_df  = pd.DataFrame(columns = col_names)
my_df

Empty DataFrame
Columns: [year, node, count, clusterID]
Index: []

In [81]:
for index, row in weighted.iterrows():
        my_df.loc[len(my_df)] = [row.year, row.source, row['count'], nodesdict[row.source.lstrip()]]
        my_df.loc[len(my_df)] = [row.year, row.target, row['count'], nodesdict[row.target.lstrip()]]
#my_df

In [82]:
for index, row in my_df.iterrows():
    #REMOVE node occurences where year is not correct - 21 rows
    if len(row.year)<>4:
        print row.year
        my_df.drop(index, inplace=True)
#my_df

cellulosic ethanol,2010
cellulosic ethanol,2010
enzymatic hydrolysis,2010
enzymatic hydrolysis,2010
ethanol,2010
ethanol,2010
hydrolysis,2010
hydrolysis,2010
anaerobic digestion,2014
anaerobic digestion,2014
biogas,2014
biogas,2014
hydrolysis,2014
hydrolysis,2014


In [83]:
#total = my_df.groupby(['year','clusterID','node']).sum()
total = my_df.groupby(['year','clusterID','node'], as_index=False, group_keys=False).sum()
total.head(30)

year  clusterID                 node  count
0   1938          5            cellulose      2
1   1938         14                sugar      2
2   1938         16                paper      2
3   1938         16                 wood      2
4   1938         19   cellulosic ethanol      4
5   1938         19              ethanol      4
6   1981         11           wood chips      1
7   1981         13         gasification      2
8   1981         16                 wood      1
9   1985         11  fixed bed gasifiers      2
10  1985         11           wood chips      1
11  1985         16                 wood      1
12  1989          5        woody biomass      1
13  1989         13         gasification      2
14  1989         16                 wood      1
15  1990          4             gasoline      1
16  1990         19                yeast      1
17  1992          4             gasoline      2
18  1992         14              bagasse      2
19  1992         14                sugar      2
20  1992         19              ethanol      2
21  1993         13         gasification      1
22  1993         16                paper      1
23  1994          4             gasoline      5
24  1994          4             seed oil      1
25  1994          4        vegetable oil      1
26  1994          5            cellulose      4
27  1994          5             rapeseed      1
28  1994         11                algae      4
29  1994         12             methanol      5

## Write treemap structure to JSONs

In [ ]:
strtotal = '{\n"name":"treemap",\n"children": [\n{'
prevyear = ''
prevcluster = ''
clID = list()
for index, row in total.iterrows():
        #print str(row.clusterID).split('\n')[0][0]
        clID = str(row.clusterID).split('\n')[0]
        #print clID
        if row.year <> prevyear:
            #new year row
            if index > 0:
                strtotal = strtotal +'\t]\n\t}\n\t]\n\t},\n\t{\n'
            strtotal = strtotal + '"name":"' + str(row.year) + '",\n'
            strtotal = strtotal + '"children": [\n{'
            if str(clID) <> prevcluster:
                #new cluster row
                strtotal = strtotal + '\t"name":"' + str(clID) + '",\n'
                strtotal = strtotal + '\t"children": [\n'
                strtotal = strtotal + '\t\t{"name":"' + row.node + '","size":' + str(row['count']) + '}'
        else:
            if str(clID) <> prevcluster:
                #new cluster row
                strtotal = strtotal +'\t]\n\t},\n\t{\n'
                strtotal = strtotal + '\t"name":"' + str(clID) + '",\n'
                strtotal = strtotal + '\t"children": [\n'
                strtotal = strtotal + '\t\t{"name":"' + row.node + '","size":' + str(row['count']) + '}'
            if clID == prevcluster:
                strtotal = strtotal + ',\n\t\t{"name":"' + row.node + '","size":' + str(row['count']) + '}'
            #strtotal = strtotal + ',\n'
            #print 'yes'
        prevyear = row.year
        prevcluster = clID
strtotal = strtotal + ']\n}\n]\n}\n]\n}'
print strtotal

In [ ]:
#variant 2 - break down years into separate json files
# strtotal = '{\n"name":"treemap",\n"children": [\n{'
prevyear = ''
prevcluster = ''
clID = list()
jsonsar = dict() #this will be an array of json strings for each treemap
year_counter = 0
for index, row in total.iterrows():
        #print str(row.clusterID).split('\n')[0][0]
        clID = str(row.clusterID).split('\n')[0]
        #print clID
        if row.year <> prevyear:
            #if new year, then store strtotal into new variable, write it to a file
            jsonsar[year_counter] = '{\n"name":"treemap",\n"children": [\n{' + strtotal + ']\n}\n]\n}\n]\n}'
            year_counter = year_counter + 1
            #reset strtotal
            strtotal = ''
#             if index > 0:
#                 strtotal = strtotal +'\t]\n\t}\n\t]\n\t},\n\t{\n'
            strtotal = strtotal + '"name":"' + str(row.year) + '",\n'
            strtotal = strtotal + '"children": [\n{'
            if str(clID) <> prevcluster:
                #new cluster row
                strtotal = strtotal + '\t"name":"' + str(clID) + '",\n'
                strtotal = strtotal + '\t"children": [\n'
                strtotal = strtotal + '\t\t{"name":"' + row.node + '","size":' + str(row['count']) + '}'
        else:
            if str(clID) <> prevcluster:
                #new cluster row
                strtotal = strtotal +'\t]\n\t},\n\t{\n'
                strtotal = strtotal + '\t"name":"' + str(clID) + '",\n'
                strtotal = strtotal + '\t"children": [\n'
                strtotal = strtotal + '\t\t{"name":"' + row.node + '","size":' + str(row['count']) + '}'
            if clID == prevcluster:
                strtotal = strtotal + ',\n\t\t{"name":"' + row.node + '","size":' + str(row['count']) + '}'
            #strtotal = strtotal + ',\n'
            #print 'yes'
        prevyear = row.year
        prevcluster = clID
        #strtotal = strtotal + ']\n}\n]\n}\n]\n}'
        #print strtotal
print jsonsar[1]
print '------------'
print jsonsar[2]
print '------------'
print jsonsar[8]

In [ ]:
for key in jsonsar:
    filename = 'treemap_' + str(key) + '.json'
    with open(filename, "w") as text_file:
        text_file.write(jsonsar[key])

## Prepare data for TimeSlider

In [ ]:
#count total number of node occurences per each year
nodesperyear = my_df.groupby(['year'], as_index=False, group_keys=False)['count'].sum()
nodesperyear

In [ ]:
#count total number of edges per each year
edgesperyear = weighted.groupby(['year'], as_index=False, group_keys=False)['count'].sum()

In [ ]:
#REMOVE node occurences where year is not correct
for index, row in edgesperyear.iterrows():
    if len(row.year)<>4:
        print row.year
        edgesperyear.drop(index, inplace=True)
edgesperyear

In [ ]:
#merge two dataframes: node occurences and edges
timeslider = pd.merge(nodesperyear, edgesperyear, on='year')
#rename resulting columns
timeslider.rename(columns={'count_x': 'nodes', 'count_y': 'edges'}, inplace=True)
timeslider

In [ ]:
#find delta for each year
deltatimeslider = timeslider
prevnode = 0
prevedge = 0
deltanode = 0
deltaedges = 0
for index, row in timeslider.iterrows():
    #find delta, set this delta to deltadf
    #first, lets do nodes
    deltanode = int(row.nodes) - prevnode
    deltatimeslider.loc[deltatimeslider.index[index], 'nodes'] = deltanode
    prevnode = int(row.nodes)
    #print index, deltanode
    #same for edges
    deltaedge = int(row.edges) - prevedge
    deltatimeslider.loc[deltatimeslider.index[index], 'edges'] = deltaedge
    prevedge = int(row.edges)
    #print index, deltaedge
deltatimeslider

In [ ]:
deltatimeslider.to_csv('timeslider.csv', sep=';')

## Extract edges and nodes for one year

In [98]:
tempyear = '2006'
oneyear = weighted.loc[weighted['year'] == tempyear]
oneyear

edges                 source  \
104           agricultural biomass,gasification,2006   agricultural biomass   
159               agricultural residues,butanol,2006  agricultural residues   
171    agricultural residues,cellulosic ethanol,2006  agricultural residues   
187               agricultural residues,ethanol,2006  agricultural residues   
203          agricultural residues,fermentation,2006  agricultural residues   
230            agricultural residues,hydrolysis,2006  agricultural residues   
243              agricultural residues,methanol,2006  agricultural residues   
265         agricultural residues,succinic acid,2006  agricultural residues   
720                  agriculture,renewable fuel,2006            agriculture   
1138                 anaerobic digestion,biogas,2006    anaerobic digestion   
1292                      animal manure,butanol,2006          animal manure   
1297                      animal manure,ethanol,2006          animal manure   
1303                 animal manure,fermentation,2006          animal manure   
1310                   animal manure,hydrolysis,2006          animal manure   
1315                     animal manure,methanol,2006          animal manure   
1324                animal manure,succinic acid,2006          animal manure   
1464                            bagasse,butanol,2006                bagasse   
1511                            bagasse,ethanol,2006                bagasse   
1528                       bagasse,fermentation,2006                bagasse   
1558                         bagasse,hydrolysis,2006                bagasse   
1576                           bagasse,methanol,2006                bagasse   
1626                      bagasse,succinic acid,2006                bagasse   
1709                       barley straw,butanol,2006           barley straw   
1720                       barley straw,ethanol,2006           barley straw   
1728                  barley straw,fermentation,2006           barley straw   
1738                    barley straw,hydrolysis,2006           barley straw   
1747                      barley straw,methanol,2006           barley straw   
1755                 barley straw,succinic acid,2006           barley straw   
1786                             barley,butanol,2006                 barley   
1808                             barley,ethanol,2006                 barley   
1823                        barley,fermentation,2006                 barley   
1842                          barley,hydrolysis,2006                 barley   
1857                            barley,methanol,2006                 barley   
1881                       barley,succinic acid,2006                 barley   
2003   biomass combustion,renewable electricity,2006     biomass combustion   
2235                              blend,ethanol,2006                  blend   
2324                             blend,methanol,2006                  blend   
2753                           cellulose,biogas,2006              cellulose   
2774                      cellulose,biopolymers,2006              cellulose   
2868                          cellulose,ethanol,2006              cellulose   
2892                     cellulose,fermentation,2006              cellulose   
2951                       cellulose,hydrolysis,2006              cellulose   
3137               cellulosic biomass,biodiesel,2006     cellulosic biomass   
3489                               cobs,butanol,2006                   cobs   
3504                               cobs,ethanol,2006                   cobs   
3514                          cobs,fermentation,2006                   cobs   
3526                            cobs,hydrolysis,2006                   cobs   
3536                              cobs,methanol,2006                   cobs   
3541                         cobs,succinic acid,2006                   cobs   
3719                           corn cob,butanol,2006               corn cob   
3733              

In [99]:
#construct list of terms that are in the edges
sourcestargets = list()
for row in oneyear.iterrows():
    #print row[1].source
    #print row[1].target
    if row[1].source not in sourcestargets:
        sourcestargets.append(row[1].source)
    if row[1].target not in sourcestargets:
        sourcestargets.append(row[1].target)
yearnodes = sourcestargets
yearnodes

[u'agricultural biomass',
 u'gasification',
 u'agricultural residues',
 u'butanol',
 u'cellulosic ethanol',
 u'ethanol',
 u'fermentation',
 u'hydrolysis',
 u'methanol',
 u'succinic acid',
 u'agriculture',
 u'renewable fuel',
 u'anaerobic digestion',
 u'biogas',
 u'animal manure',
 u'bagasse',
 u'barley straw',
 u'barley',
 u'biomass combustion',
 u'renewable electricity',
 u'blend',
 u'cellulose',
 u'biopolymers',
 u'cellulosic biomass',
 u'biodiesel',
 u'cobs',
 u'corn cob',
 u'corn stover',
 u'corn',
 u'energy crops',
 u'forest residues',
 u'forestry',
 u'biofuels for transport',
 u'free fatty acid',
 u'sng',
 u'grain',
 u'grains',
 u'grass',
 u'husk',
 u'industrial waste',
 u'liquefaction',
 u'bio-oil',
 u'manure',
 u'msw',
 u'municipal solid waste',
 u'natural gas',
 u'gasoline',
 u'solvents',
 u'pal waste',
 u'palm',
 u'paper',
 u'rapeseed',
 u'residues',
 u'rice straw',
 u'sawdust',
 u'seeds',
 u'sewage',
 u'biomass gasification',
 u'gas cleaning',
 u'sorghum',
 u'soy',
 u'stover

In [100]:
#check if this terms are in node list, if not - remove
for term in yearnodes:
    #print term
    if term not in nodes:
        print "term: " + term + " is removed"
        yearnodes.remove(term)
yearnodes

[u'agricultural biomass',
 u'gasification',
 u'agricultural residues',
 u'butanol',
 u'cellulosic ethanol',
 u'ethanol',
 u'fermentation',
 u'hydrolysis',
 u'methanol',
 u'succinic acid',
 u'agriculture',
 u'renewable fuel',
 u'anaerobic digestion',
 u'biogas',
 u'animal manure',
 u'bagasse',
 u'barley straw',
 u'barley',
 u'biomass combustion',
 u'renewable electricity',
 u'blend',
 u'cellulose',
 u'biopolymers',
 u'cellulosic biomass',
 u'biodiesel',
 u'cobs',
 u'corn cob',
 u'corn stover',
 u'corn',
 u'energy crops',
 u'forest residues',
 u'forestry',
 u'biofuels for transport',
 u'free fatty acid',
 u'sng',
 u'grain',
 u'grains',
 u'grass',
 u'husk',
 u'industrial waste',
 u'liquefaction',
 u'bio-oil',
 u'manure',
 u'msw',
 u'municipal solid waste',
 u'natural gas',
 u'gasoline',
 u'solvents',
 u'pal waste',
 u'palm',
 u'paper',
 u'rapeseed',
 u'residues',
 u'rice straw',
 u'sawdust',
 u'seeds',
 u'sewage',
 u'biomass gasification',
 u'gas cleaning',
 u'sorghum',
 u'soy',
 u'stover

In [101]:
#nodeindex = {0:'zero',1:'one'}
#create dictionary to map indexes to nodes
yearnodeindex = {}
for i in range(len(yearnodes)):
    yearnodeindex[i] = yearnodes[i]
yearnodeindex

{0: u'agricultural biomass',
 1: u'gasification',
 2: u'agricultural residues',
 3: u'butanol',
 4: u'cellulosic ethanol',
 5: u'ethanol',
 6: u'fermentation',
 7: u'hydrolysis',
 8: u'methanol',
 9: u'succinic acid',
 10: u'agriculture',
 11: u'renewable fuel',
 12: u'anaerobic digestion',
 13: u'biogas',
 14: u'animal manure',
 15: u'bagasse',
 16: u'barley straw',
 17: u'barley',
 18: u'biomass combustion',
 19: u'renewable electricity',
 20: u'blend',
 21: u'cellulose',
 22: u'biopolymers',
 23: u'cellulosic biomass',
 24: u'biodiesel',
 25: u'cobs',
 26: u'corn cob',
 27: u'corn stover',
 28: u'corn',
 29: u'energy crops',
 30: u'forest residues',
 31: u'forestry',
 32: u'biofuels for transport',
 33: u'free fatty acid',
 34: u'sng',
 35: u'grain',
 36: u'grains',
 37: u'grass',
 38: u'husk',
 39: u'industrial waste',
 40: u'liquefaction',
 41: u'bio-oil',
 42: u'manure',
 43: u'msw',
 44: u'municipal solid waste',
 45: u'natural gas',
 46: u'gasoline',
 47: u'solvents',
 48: u'pa

In [102]:
zero_data = np.zeros(shape=(len(yearnodes),len(yearnodes)))
yearadjacency = pd.DataFrame(zero_data, index = yearnodeindex, columns=yearnodes)
yearadjacency.rename(index=yearnodeindex, inplace=True)
yearadjacency

agricultural biomass  gasification  \
agricultural biomass                     0.0           0.0   
gasification                             0.0           0.0   
agricultural residues                    0.0           0.0   
butanol                                  0.0           0.0   
cellulosic ethanol                       0.0           0.0   
ethanol                                  0.0           0.0   
fermentation                             0.0           0.0   
hydrolysis                               0.0           0.0   
methanol                                 0.0           0.0   
succinic acid                            0.0           0.0   
agriculture                              0.0           0.0   
renewable fuel                           0.0           0.0   
anaerobic digestion                      0.0           0.0   
biogas                                   0.0           0.0   
animal manure                            0.0           0.0   
bagasse                                  0.0           0.0   
barley straw                             0.0           0.0   
barley                                   0.0           0.0   
biomass combustion                       0.0           0.0   
renewable electricity                    0.0           0.0   
blend                                    0.0           0.0   
cellulose                                0.0           0.0   
biopolymers                              0.0           0.0   
cellulosic biomass                       0.0           0.0   
biodiesel                                0.0           0.0   
cobs                                     0.0           0.0   
corn cob                                 0.0           0.0   
corn stover                              0.0           0.0   
corn                                     0.0           0.0   
energy crops                             0.0           0.0   
forest residues                          0.0           0.0   
forestry                                 0.0           0.0   
biofuels for transport                   0.0           0.0   
free fatty acid                          0.0           0.0   
sng                                      0.0           0.0   
grain                                    0.0           0.0   
grains                                   0.0           0.0   
grass                                    0.0           0.0   
husk                                     0.0           0.0   
industrial waste                         0.0           0.0   
liquefaction                             0.0           0.0   
bio-oil                                  0.0           0.0   
manure                                   0.0           0.0   
msw                                      0.0           0.0   
municipal solid waste                    0.0           0.0   
natural gas                              0.0           0.0   
gasoline                                 0.0           0.0   
solvents                                 0.0           0.0   
pal waste                                0.0           0.0   
palm                                     0.0           0.0   
paper                                    0.0           0.0   
rapeseed                                 0.0           0.0   
residues                                 0.0           0.0   
rice straw                               0.0           0.0   
sawdust                                  0.0           0.0   
seeds                                    0.0           0.0   
sewage                                   0.0           0.0   
biomass gasification                     0.0           0.0   
gas cleaning                             0.0           0.0   
sorghum                                  0.0           0.0   
soy                                      0.0           0.0   
stover                                   0.0           0.0   
straw                                    0.0           0.0   
sugar                                    0.0           0

In [103]:
for index, row in oneyear.iterrows():
    #if nodes.isin(row.source) and nodes.isin(row.target) :
    #print row['count']
    if row.source in yearnodes and row.target in yearnodes:
        yearadjacency.at[row.source,row.target] = row['count']
        yearadjacency.at[row.target,row.source] = row['count']
    else:
        print (row.source + ":" + row.target)
yearadjacency
%store yearadjacency
%store yearnodes

Stored 'yearadjacency' (DataFrame)
Stored 'yearnodes' (list)


In [104]:
pickle_in = open("nodes_clustered.pickle","rb")
nodes_clustered = pickle.load(pickle_in)
nodes_clustered

0  cluster
0                         vegetable oil        4
1                     woodwaste/bagasse        0
2                           natural gas       14
3                       various grasses       19
4                        nonedible oils       17
5                           animal fats       12
6                                 paper       16
7                        ponderosa pine       19
8                            grass seed       19
9                                   osb       14
10                          paper waste       12
11                             corn cob       13
12                       energy grasses       19
13                     logging residues       19
14                               willow       16
15                           crop waste       13
16                             firewood       13
17                             jatropha        4
18                    sugarcane bagasse       19
19                                sugar       14
20                                 wood       16
21                municipal solid waste       14
22                          banna grass       13
23                            waste oil       12
24                               barley       19
25                               starch        5
26                      coniferous wood        7
27                             corn oil       14
28                           wood waste        4
29                          corn stalks        4
30                        yellow grease       12
31                             molasses       19
32                            woodchips        7
33                           food waste        4
34                      citrus residues       17
35                           wood chips       11
36                       cotton residue       13
37                     industrial waste        7
38                          corn stover       14
39                            waste fat       17
40                  waste vegetable oil       13
41                               tallow       12
42                               sewage       13
43                           white pine       13
44                             hardwood        7
45                        loblolly pine       19
46                           miscanthus       19
47                                 palm       14
48                                 milo       11
49                                 bark        4
50                          agriculture       14
51                             textiles        7
52                          beef tallow       12
53                         animal waste       14
54                                 cobs       14
55                      forest residues       13
56                      grass clippings       19
57                              plywood       13
58                          dry biomass        4
59                 southern yellow pine       13
60                      free fatty acid        7
61                          trap grease       17
62   woody and agricultural by-products       19
63                 syngas from gasifier       16
64                            cellulose        5
65                                wheat       11
66                        organic waste       14
67                           oil plants       17
68                                 corn        4
69                        animal manure       14
70                                 dung       14
71                   agricultural waste       14
72                       elephant grass       19
73                biogas from landfills       17
74                   waste water sludge       14
75                                algae       11
76                           rice straw       19
77                         barley straw       19
78                           Giant reed       17
79                           rice hulls       19
80                           canola oil        7
81                  

In [93]:
filename = 'terms_by_clusters.csv'
nodes_clustered.to_csv(filename, sep=',')

In [94]:
nodes
print(len(nodes))

281


## Write the file for D3

In [105]:
strjson = '{"nodes":['
for node in yearnodes:
    print node
    #print nodeindex(node)
    #print nodes_clustered.cluster[yearnodes.index('natural gas')]
    strjson = strjson + '{"name":"' + node + '","group":' + str(nodes_clustered.cluster[nodes.index(node)]) + '},'
#remove last comma from json
strjson = strjson[:-1]
print strjson

agricultural biomass
gasification
agricultural residues
butanol
cellulosic ethanol
ethanol
fermentation
hydrolysis
methanol
succinic acid
agriculture
renewable fuel
anaerobic digestion
biogas
animal manure
bagasse
barley straw
barley
biomass combustion
renewable electricity
blend
cellulose
biopolymers
cellulosic biomass
biodiesel
cobs
corn cob
corn stover
corn
energy crops
forest residues
forestry
biofuels for transport
free fatty acid
sng
grain
grains
grass
husk
industrial waste
liquefaction
bio-oil
manure
msw
municipal solid waste
natural gas
gasoline
solvents
pal waste
palm
paper
rapeseed
residues
rice straw
sawdust
seeds
sewage
biomass gasification
gas cleaning
sorghum
soy
stover
straw
sugar
switchgrass
vegetable oil
waste oil
waste vegetable oil
waste
pyrolysis
wheat straw
wheat
wood chips
pellets
wood
yeast
{"nodes":[{"name":"agricultural biomass","group":7},{"name":"gasification","group":13},{"name":"agricultural residues","group":16},{"name":"butanol","group":19},{"name":"cellu

In [108]:
stredges = '],"links":['
for source in yearnodes:
    #print source + "--------------"
    for target in yearnodes:
        #print target
        if yearadjacency[source][target] > 0:
            #strpair = '{"source":' + source + ',"target":' + target + ',"value":' + str(adjacency[source][target]) + '},'
            strpair = '{"source":"' + source + '","target":"' + target + '","value":' + str(yearadjacency[source][target]) + '},'
            stredges = stredges + strpair
stredges = stredges[:-1]
stredges = stredges + "]}"
print stredges

],"links":[{"source":"agricultural biomass","target":"gasification","value":1.0},{"source":"gasification","target":"agricultural biomass","value":1.0},{"source":"gasification","target":"sng","value":1.0},{"source":"gasification","target":"industrial waste","value":1.0},{"source":"gasification","target":"msw","value":1.0},{"source":"gasification","target":"natural gas","value":1.0},{"source":"gasification","target":"sewage","value":1.0},{"source":"gasification","target":"straw","value":2.0},{"source":"gasification","target":"waste","value":1.0},{"source":"gasification","target":"wheat straw","value":1.0},{"source":"gasification","target":"wheat","value":1.0},{"source":"agricultural residues","target":"butanol","value":1.0},{"source":"agricultural residues","target":"cellulosic ethanol","value":1.0},{"source":"agricultural residues","target":"ethanol","value":3.0},{"source":"agricultural residues","target":"fermentation","value":2.0},{"source":"agricultural residues","target":"hydrolysis

In [109]:
filename = 'clustered_' + tempyear + '.json'
with open(filename, 'w') as outfile:
    outfile.write(strjson + stredges)